### References

* Chatbot with TF: https://chatbotsmagazine.com/contextual-chat-bots-with-tensorflow-4391749d0077
* Good reference list for reading: http://www.wildml.com/2016/04/deep-learning-for-chatbots-part-1-introduction/


### Options:
* Use categories from semtype tagging to identify

## Initialize

In [1]:
# Utility
import sys,os
import time

import pandas as pd

# Custom
from processing import tag_utterances
from processing import load_sem_types

## NLP
import spacy

# Set absolute path the QuickUMLS Server
abs_path_umls = '/Users/austinpowell/Google_Drive/kp_datascience/doctor_notes/ontology/UMLS'
abs_path_data_umls = '/Users/austinpowell/Google_Drive/kp_datascience/doctor_notes/ontology/UMLS/QuickUMLS_data'
sys.path.append(abs_path_umls+'/QuickUMLS')
from quickumls import QuickUMLS
tagger = QuickUMLS(abs_path_data_umls)

In [2]:
path_to_data = '../data/reddit_comments_askDocs_2014_to_2018_03.gz'
df = pd.read_csv(path_to_data,low_memory=False)
print('Shape',df.shape)
df.head(2)

Shape (557648, 21)


body score_hidden archived  \
0  for a manlet such as yourself I'd recommend at...          NaN      NaN   
1                 Thank you very much for answering!          NaN      NaN   

  name author                     author_flair_text  downs  created_utc  \
0  NaN    -Ai  This user has not yet been verified.    NaN   1513411674   
1  NaN    -SY  This user has not yet been verified.    NaN   1445798103   

  subreddit_id    link_id      ...       score  retrieved_on  \
0     t5_2xtuc  t3_7k5x2h      ...           0  1.514772e+09   
1     t5_2xtuc  t3_3q697b      ...           2  1.447190e+09   

   controversiality  gilded       id subreddit  ups  distinguished  \
0                 0       0  drbt2db   AskDocs  NaN            NaN   
1                 0       0  cwcfjpr   AskDocs  2.0            NaN   

  author_flair_css_class removal_reason  
0                default            NaN  
1                default            NaN  

[2 rows x 21 columns]

In [3]:
# Load semantic types
sem_type_dict = load_sem_types('../data/SemGroups_2013.txt')

In [8]:
t = tagger.nlp(df['body'].iloc[4])
t.text

"She's had it for 8 months, we've never had any issues with it before."

In [9]:
t = tagger.nlp(t.text)

s = t
matches= tagger.match(s, best_match=True, ignore_syntax=False)
for match in matches:
    dir(match)
for m in match:
    print(m)

{'start': 19, 'end': 25, 'ngram': 'months', 'term': 'month', 'cui': 'C1561542', 'similarity': 0.75, 'semtypes': {'T170'}, 'preferred': 1}


In [21]:
sd = load_sem_types('../data/SemGroups_2013.txt')
m['semtypes']

AttributeError: 'set' object has no attribute 'text'

In [11]:
import importlib
from processing import tag_utterances
from processing import load_sem_types

tag_utterances(1, t.text, tagger)

{'T170'}


[[1, 19, 25, 'month', 'C1561542', 0.75, {'Intellectual Product'}]]

In [31]:
%%time
print('Iterating over every document')
#Iterate over every document and extract the concepts
i=-1        
result = []
for idx,doc in  enumerate(df['body']):

    if idx % 100 == 0:
        print("Documents processed: {}".format(idx))
    try:
        i+=1
        annotations = tag_utterances(i,doc,tagger)
        result.extend(annotations)
    except Exception as e:
        print(e)
        
df_matches = pd.DataFrame(data=result, columns =['document','start','end','term','cui','similarity','semtypes'])
df_matches.sort_values(by=['document','start'],inplace=True)

Iterating over every document
Documents processed: 0
Documents processed: 5
Documents processed: 10
Documents processed: 15
Documents processed: 20
Documents processed: 25
Documents processed: 30
Documents processed: 35
Documents processed: 40
Documents processed: 45
Documents processed: 50
Documents processed: 55
Documents processed: 60
Documents processed: 65
Documents processed: 70
Documents processed: 75
Documents processed: 80
Documents processed: 85
Documents processed: 90
Documents processed: 95
Documents processed: 100
Documents processed: 105
Documents processed: 110
Documents processed: 115
Documents processed: 120
Documents processed: 125
Documents processed: 130
Documents processed: 135
Documents processed: 140
Documents processed: 145
Documents processed: 150
Documents processed: 155
Documents processed: 160
Documents processed: 165
Documents processed: 170
Documents processed: 175
Documents processed: 180
Documents processed: 185
Documents processed: 190
Documents process

In [35]:
df_matches.head()

document  start  end            term       cui  similarity  \
2          0     62   67           water  C0043047         1.0   
0          0     89  103  hours of sleep  C2937255         1.0   
3          0    105  108             cut  C0000925         1.0   
1          0    140  153   sodium intake  C0489645         1.0   
11         2     11   17          tested  C0392366         1.0   

                                             semtypes  
2       {Pharmacologic Substance, Inorganic Chemical}  
0                                           {Finding}  
3                               {Injury or Poisoning}  
1                                {Clinical Attribute}  
11  {Body Part, Organ, or Organ Component, Intelle...

In [33]:
df.shape

(557648, 21)

In [6]:
df.head()

body score_hidden archived  \
0  for a manlet such as yourself I'd recommend at...          NaN      NaN   
1                 Thank you very much for answering!          NaN      NaN   
2  Never been tested for that.  I was hoping the ...          NaN      NaN   
3  She said her constant abdominal pain is a 6, t...          NaN      NaN   
4  She's had it for 8 months, we've never had any...          NaN      NaN   

  name author                     author_flair_text  downs  created_utc  \
0  NaN    -Ai  This user has not yet been verified.    NaN   1513411674   
1  NaN    -SY  This user has not yet been verified.    NaN   1445798103   
2  NaN    -o2  This user has not yet been verified.    NaN   1461952470   
3  NaN    05P  This user has not yet been verified.    NaN   1504214332   
4  NaN    05P  This user has not yet been verified.    NaN   1504217835   

  subreddit_id    link_id      ...       score  retrieved_on  \
0     t5_2xtuc  t3_7k5x2h      ...           0  1.514772e+09   
1     t5_2xtuc  t3_3q697b      ...           2  1.447190e+09   
2     t5_2xtuc  t3_4gz1fi      ...           1  1.463777e+09   
3     t5_2xtuc  t3_6x9jk0      ...           1  1.504553e+09   
4     t5_2xtuc  t3_6x9jk0      ...           1  1.504554e+09   

   controversiality  gilded       id subreddit  ups  distinguished  \
0                 0       0  drbt2db   AskDocs  NaN            NaN   
1                 0       0  cwcfjpr   AskDocs  2.0            NaN   
2                 0       0  d2mce34   AskDocs  1.0            NaN   
3                 0       0  dme9lzr   AskDocs  NaN            NaN   
4                 0       0  dmecohs   AskDocs  NaN            NaN   

  author_flair_css_class removal_reason  
0                default            NaN  
1                default            NaN  
2                default            NaN  
3                default            NaN  
4                default            NaN  

[5 rows x 21 columns]

In [9]:
df.author_flair_text.value_counts()

This user has not yet been verified.     352466
Physician                                 26484
Medical Student                           13399
B.S., Medical Lab Sciences                 3069
FY1 Doctor                                 2860
Moderator                                  2644
Registered Nurse                           2589
Emergency Medical Technician               2023
Surgeon                                    1765
Surgeon | Moderator                        1710
Orthopaedic Surgeon                        1569
Psychiatrist                               1513
Dermatologist                              1481
Doctor (A&amp;E)                           1435
Pharm.D. - Hospital Pharmacist             1056
Emergency Physician                        1027
Nursing Graduate, RPN                       803
Pharm.D.                                    748
Nursing Student                             735
Occupational Therapist                      727
Anesthesiologist                        

### Predicting Author

In [16]:
df['is_clinician'] = df['author_flair_text'].apply(lambda r: 0 if r =='This user has not yet been verified.' else 1)
print(df['is_clinician'].mean())
print(df['is_clinician'].value_counts())

0.36794178406449946
0    352466
1    205182
Name: is_clinician, dtype: int64


In [6]:
nlp_pipe_umls = spacy('e')

TypeError: 'float' object is not iterable

In [ ]:
model.train(num_epochs=100)

In [ ]:
model.generate_tsne()